В этом ноутбуке мы попытаемся прогнозировать данные по транзакциям с использованием библиотеки пророк

Загрузим библиотеки и данные

In [9]:
# Load libraries
import numpy as np
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
import pandas as pd
pd.set_option('display.max_rows', 10)
pd.set_option('display.max_columns', 70)
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode()

#from fbprophet import Prophet
from prophet import Prophet

%time df_transactions = pd.read_csv('data/transactions.csv')
%time df_holidays_events = pd.read_csv('data/holidays_events.csv')

print('Data and libraries are loaded.')

CPU times: user 11.3 ms, sys: 4.54 ms, total: 15.9 ms
Wall time: 16.4 ms
CPU times: user 990 µs, sys: 203 µs, total: 1.19 ms
Wall time: 1.46 ms
Data and libraries are loaded.


In [2]:
#conda install fbprophet

In [3]:
df_transactions = pd.read_csv('./data/transactions.csv')
df_transactions

date  store_nbr  transactions
0      2013-01-01         25           770
1      2013-01-02          1          2111
2      2013-01-02          2          2358
3      2013-01-02          3          3487
4      2013-01-02          4          1922
...           ...        ...           ...
83483  2017-08-15         50          2804
83484  2017-08-15         51          1573
83485  2017-08-15         52          2255
83486  2017-08-15         53           932
83487  2017-08-15         54           802

[83488 rows x 3 columns]

Если мы посмотрим на данные транзакций, транзакции сгруппированы по номерам магазинов. Сейчас мы упростим это и сгруппируем их по дате. 

In [4]:
transactions = df_transactions.groupby('date')['transactions'].sum()
py.iplot([go.Scatter(
    x=transactions.index,
    y=transactions
)])

Хорошо заметно влияние сезонности и праздников на общий объем транзакций.

Теперь давайте попробуем библиотеку пророк и посмотрим, насколько хорошо она предсказывает. Но перед этим мы должны подготовить данные. Согласно документации:

> Prophet следует API модели sklearn. Мы создаем экземпляр класса Prophet, а затем вызываем его методы соответствия и прогнозирования.
> Входными данными для Prophet всегда является фрейм данных с двумя столбцами: ** ds ** и ** y **. Столбец ds (отметка даты) должен содержать дату или дату и время (это нормально). Столбец ** y ** должен быть числовым и представлять измерение, которое мы хотим спрогнозировать.

In [5]:
transactions = pd.DataFrame(transactions).reset_index()
transactions.columns = ['ds', 'y']
transactions

ds      y
0     2013-01-01    770
1     2013-01-02  93215
2     2013-01-03  78504
3     2013-01-04  78494
4     2013-01-05  93573
...          ...    ...
1677  2017-08-11  89551
1678  2017-08-12  89927
1679  2017-08-13  85993
1680  2017-08-14  85448
1681  2017-08-15  86561

[1682 rows x 2 columns]

In [10]:
m = Prophet()
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)
forecast

23:06:35 - cmdstanpy - INFO - Chain [1] start processing
23:06:36 - cmdstanpy - INFO - Chain [1] done processing


ds         trend    yhat_lower     yhat_upper   trend_lower  \
0    2013-01-01  77854.679129  75453.974523   97257.979845  77854.679129   
1    2013-01-02  77864.798423  75396.162021   95253.504846  77864.798423   
2    2013-01-03  77874.917717  70037.752031   89918.790730  77874.917717   
3    2013-01-04  77885.037011  72757.501360   93848.978310  77885.037011   
4    2013-01-05  77895.156306  85822.211690  105727.514783  77895.156306   
...         ...           ...           ...            ...           ...   
2042 2018-08-11  97232.864606  96906.881229  116558.158821  96296.139486   
2043 2018-08-12  97249.644377  90553.708008  111838.756220  96309.373565   
2044 2018-08-13  97266.424148  81033.014005  101315.994974  96322.607644   
2045 2018-08-14  97283.203919  79069.617673  100229.952196  96335.841723   
2046 2018-08-15  97299.983691  80366.225551  100274.206057  96349.075802   

       trend_upper  additive_terms  additive_terms_lower  \
0     77854.679129     8040.826475           8040.826475   
1     77864.798423     7135.308776           7135.308776   
2     77874.917717     1625.813457           1625.813457   
3     77885.037011     5209.987243           5209.987243   
4     77895.156306    17886.846301          17886.846301   
...            ...             ...                   ...   
2042  98219.711928     9931.106009           9931.106009   
2043  98240.509487     4529.979301           4529.979301   
2044  98261.256434    -6013.238125          -6013.238125   
2045  98281.207701    -7748.348825          -7748.348825   
2046  98301.001111    -6532.094548          -6532.094548   

      additive_terms_upper        weekly  weekly_lower  weekly_upper  \
0              8040.826475  -4840.259008  -4840.259008  -4840.259008   
1              7135.308776  -3740.633613  -3740.633613  -3740.633613   
2              1625.813457  -7236.249924  -7236.249924  -7236.249924   
3              5209.987243  -1661.270143  -1661.270143  -1661.270143   
4             17886.846301  12952.785251  12952.785251  12952.785251   
...                    ...           ...           ...           ...   
2042           9931.106009  12952.785251  12952.785251  12952.785251   
2043           4529.979301   7553.262585   7553.262585   7553.262585   
2044          -6013.238125  -3027.635148  -3027.635148  -3027.635148   
2045          -7748.348825  -4840.259008  -4840.259008  -4840.259008   
2046          -6532.094548  -3740.633613  -3740.633613  -3740.633613   

            yearly  yearly_lower  yearly_upper  multiplicative_terms  \
0     12881.085483  12881.085483  12881.085483                   0.0   
1     10875.942388  10875.942388  10875.942388                   0.0   
2      8862.063382   8862.063382   8862.063382                   0.0   
3      6871.257386   6871.257386   6871.257386                   0.0   
4      4934.061050   4934.061050   4934.061050                   0.0   
...            ...           ...           ...                   ...   
2042  -3021.679242  -3021.679242  -3021.679242                   0.0   
2043  -3023.283284  -3023.283284  -3023.283284                   0.0   
2044  -2985.602977  -2985.602977  -2985.602977                   0.0   
2045  -2908.089817  -2908.089817  -2908.089817                   0.0   
2046  -2791.460936  -2791.460936  -2791.460936                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper           yhat  
0                            0.0                         0.0   85895.505604  
1                            0.0                         0.0   85000.107199  
2                            0.0                         0.0   79500.731175  
3                            0.0                         0.0   83095.024254  
4                            0.0                         0.0   95782.002607  
...                          ...                         ...            ...  
2042                         0.0                         0.0  107163.970615  
2043                     

In [11]:
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

In [12]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )

RMSE: 7902.786476


Как видно на графике выше, прогноз довольно хороший и согласуется с взлетами и падениями данных. Вы можете увеличить график, выбрав область масштабирования с помощью мыши.

Но тенденция довольно жесткая, она не учитывает под-тренды середины года. В первой половине года тенденция нарастает, а затем немного замедляется. Сделаем тренд немного гибким. Если тренд является переобученным (слишком большая гибкость) или недостаточными (недостаточная гибкость), вы можете отрегулировать силу разреженности перед использованием входного аргумента ** changepoint_prior_scale **. По умолчанию этот параметр установлен на 0,05. Его увеличение сделает тренд более гибким. (https://facebook.github.io/prophet/docs/trend_changepoints.html)

In [13]:
m = Prophet(changepoint_prior_scale=2.5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

23:06:46 - cmdstanpy - INFO - Chain [1] start processing
23:06:47 - cmdstanpy - INFO - Chain [1] done processing


In [14]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7859.180297


Теперь добавим в модель больше сезонности. Как мы видим, Пророк рассчитывает еженедельную и годовую сезонность. Нам не нужна ежедневная сезонность, потому что у нас нет внутридневных данных для этого случая. Достаточно просто добавить ежемесячную сезонность.

In [15]:
m = Prophet(changepoint_prior_scale=2.5)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

23:06:55 - cmdstanpy - INFO - Chain [1] start processing
23:06:55 - cmdstanpy - INFO - Chain [1] done processing


In [16]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 7683.640666


Пришло время добавить в нашу модель влияние праздников. Сначала нам нужно настроить формат данных. Пророку нужны два столбца (праздник и ds) и строка для каждого наступления праздника. Так же можно включить столбцы lower_window и upper_window, которые продлевают праздничные дни до дней «[lower_window, upper_window]» вокруг даты. 

In [18]:
df_holidays_events = pd.read_csv('./data/holidays_events.csv')
df_holidays_events.head()

date     type    locale locale_name                    description  \
0  2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1  2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2  2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3  2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4  2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   

   transferred  
0        False  
1        False  
2        False  
3        False  
4        False

In [19]:
holidays = df_holidays_events[df_holidays_events['transferred'] == False][['description', 'date']]
holidays.columns = ['holiday', 'ds']
#holidays['lower_window'] = 0
#holidays['upper_window'] = 0
holidays

holiday          ds
0               Fundacion de Manta  2012-03-02
1    Provincializacion de Cotopaxi  2012-04-01
2              Fundacion de Cuenca  2012-04-12
3        Cantonizacion de Libertad  2012-04-14
4        Cantonizacion de Riobamba  2012-04-21
..                             ...         ...
345                      Navidad-3  2017-12-22
346                      Navidad-2  2017-12-23
347                      Navidad-1  2017-12-24
348                        Navidad  2017-12-25
349                      Navidad+1  2017-12-26

[338 rows x 2 columns]

In [20]:
m = Prophet(changepoint_prior_scale=2.5, holidays=holidays)
m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(transactions)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)

23:07:38 - cmdstanpy - INFO - Chain [1] start processing
23:07:39 - cmdstanpy - INFO - Chain [1] done processing


In [21]:
# Вычислим среднеквадратичную ошибку.
print('RMSE: %f' % np.sqrt(np.mean((forecast.loc[:1682, 'yhat']-transactions['y'])**2)) )
py.iplot([
    go.Scatter(x=transactions['ds'], y=transactions['y'], name='y'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat'], name='yhat'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_upper'], fill='tonexty', mode='none', name='upper'),
    go.Scatter(x=forecast['ds'], y=forecast['yhat_lower'], fill='tonexty', mode='none', name='lower'),
    go.Scatter(x=forecast['ds'], y=forecast['trend'], name='Trend')
])

RMSE: 4929.702730


Нам удалось спрогнозировать всплески на новогодний период. Модель не смогла уловить резкий скачок вниз на 4 января 2016 года, поэтому она не смогла успешно спрогнозировать 1 января 2017 года. 
Это объясняется тем, что 4 января 2016 года не было выходных. Но модель хорошо предсказывает продажи на 24 декабря. А также прогнозируемый период после 15 августа 2017 года выглядит неплохо.


Prophet - это довольно простая в использовании библиотека для прогнозирования данных временных рядов, которая использует для этого только предыдущие данные и праздники. Есть другие функции и параметры, такие как прогнозы насыщения, интервалы неопределенности и т. Д., Которые мы здесь не рассматривали. Вы можете прочитать больше в статье https://peerj.com/preprints/3190.pdf.